In [1]:
# make dataframes from txt data
# each txt contains one tagesschau transcription
import os
import pandas as pd
import numpy as np
from wordcloud import WordCloud
from nltk.stem.snowball import SnowballStemmer
import nltk
from nltk.corpus import stopwords
#nltk.download('stopwords')
from sklearn.feature_extraction.text import CountVectorizer
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.decomposition import LatentDirichletAllocation as LDA
import warnings
import time
warnings.simplefilter("ignore", DeprecationWarning)
import matplotlib.pyplot as plt
import spacy
import de_core_news_lg
nlp = de_core_news_lg.load(disable=['parser'])
#nlp.add_pipe(nlp.create_pipe('sentencizer'))
import datetime
from joblib import Parallel, delayed
from functools import partial
from gensim import corpora,models
import re
import pyLDAvis.gensim
# Enable in-notebook visualizations
%matplotlib inline
pyLDAvis.enable_notebook()
pd.options.display.max_rows = 10


# load the s2t transcriptions
def load_transcriptions(path):
    os.chdir(path)
    transcriptions = os.listdir()#[:30]
    return transcriptions

# preprocessing for topic modelling, in this case LDA (latent dirichlet allocation)
def lemmatize_pipe(doc):
    lemma_list = [tok.lemma_ for tok in doc]# if str(tok).isalpha] #usually str(tok.lemma_).lower()
    return lemma_list

def preprocess_pipe(texts,nouns_array):#,non_nouns_array):
    preproc_pipe = []
    #non_nouns = non_nouns_array
    nounss = nouns_array
    for doc in nlp.pipe(texts, batch_size=int(len(transcriptions)/n_cpu_cores),n_process=int(n_cpu_cores)):
        preproc_pipe.append(lemmatize_pipe(doc))
        #non_nouns.extend([word for word in doc if word.pos_!='NOUN'])
        #nounss.append([str(chunk.text) for chunk in doc.noun_chunks])
        nounss.append([str(word) for word in doc if not word.is_stop and str(word).isalpha()])# and word.pos_=='NOUN'])# or word.pos_=='ADJ'])
    return preproc_pipe,nounss#,non_nouns

def preprocess_transcriptions(transcripts_df,number_cpu_cores=os.cpu_count()-1):
    
    manual_stopwords = ['wetter','wochentag','monat','ziel','zahl','stunden','weg','fernsehen','praesident',
                        'damen','herren','menschen','land','abend','grad','nacht','euro','geld','regierung',
                       'millionen','unternehmen','tagesthemen','angaben','himmelsrichtung',
                       'milliarden','tagesschau','woche','wochen','leben','%','welt','€','sueden',
                        'mitarbeiter','montag','welt','richtung','deutsche','deutschen','mal',
                        'moeglichkeit','fast','klar','meist','letzten','mehrere','steht','bleibt','sieht',
                        'deutlich','gestern','sehen','kritik','guten','folgen','neues','geben','bislang',
                       'eigentlich','teilweise','lassen','suedosten','gekommen','insgesamt','sagen','erneut',
                        'frauen','bringen','nachmittag','naechsten','mindestens','krise']
    
    # init array for all nouns found by spacy
    nounss = []
    #print("Use: "+str(len(transcriptions))+" transcriptions, preprocess them (and perform LDA (Latent Dirichlet Allocation))")
    # use following line instead of the line after the folowing to use "tagesschau" only
    #df = pd.DataFrame(index=[i for i in range(len(transcriptions)) if "tagessschau" in transcriptions[i]], columns=['transcriptionName','content','year','month','day'])
    df = pd.DataFrame(index=[i for i in range(len(transcriptions))], columns=['transcriptionName','content','preprocessed','year','month','day'])
    for transcription in range(len(transcriptions)):
        # use following line to use "tagesschau" only
        #if "tagesschau" in str(transcriptions[transcription]):
        if transcription>-1: #placeholder for above line
            with open(transcriptions[transcription], "r") as f:
                df.loc[transcription,'transcriptionName'] = str(transcriptions[transcription])
                df.loc[transcription,'content'] = f.read()
    df = df.reset_index()
    df1=df.copy()
    for transcript in range(len(df)):
        # remove "newline" and punctuation
        #print(df.loc[transcript,'content'])
        df.loc[transcript,'content'] = df.loc[transcript,'content'].replace("\n","").replace(".","")

    sta = datetime.datetime.now()
    df['content'],nounss = preprocess_pipe(df['content'],nounss)#,non_nouns)
    print("lemmatizing+filtering out nouns needs:",(datetime.datetime.now()-sta).total_seconds(),"seconds")

    for i in range(len(nounss)):
        nounss[i] = [noun.lower() for noun in nounss[i]]

    manual = [[['wetter'],['sonne','regen','wind','schnee','schauer','luft','wolken','gewitter','gewittern']],
              [['himmelsrichtung'],['norden','sueden','osten','westen']],
              [['wochentag'],['montag','dienstag','mittwoch','donnerstag','freitag','samstag','sonntag']],
              [['monat'],['januar','februar','maerz','april','mai','juni','juli','august','september','oktober','november','dezember']],
              [['corona'],['korona']]]
    start_manual=datetime.datetime.now()
    for i in range(len(nounss)):
        for j in range(len(nounss[i])):
            nounss[i][j] = nounss[i][j].replace("ä",'ae').replace("ü","ue").replace("ö","oe").replace("ß","ss")
            for k in manual:
                for l in range(len(k[1])):
                    if k[1][l]==nounss[i][j]:
                        nounss[i][j] = k[0][0]
    end_manual=datetime.datetime.now()
    print("replacing e.g. 'sonne','regen'... by 'wetter' needs:",
          (end_manual-start_manual).total_seconds(),"seconds")    
        
    manualStopWords = manual_stopwords
    removeWords = []
    for i in range(len(nounss)):
        for j in range(len(nounss[i])):
            for k in manualStopWords:
                if k in nounss[i][j]:
                    #print("nounss in manualS",nounss[i])
                    removeWords.append(nounss[i][j])
    removeWords = list(dict.fromkeys(removeWords))

    for i in range(len(nounss)):
        nounss[i] = [word for word in nounss[i] if word not in removeWords]
        
    for i in range(len(nounss)):
        nounss[i] = (','.join(nounss[i])).replace(','," ")
    
    #merge all docs into dataframe
    for i in range(len(df)):
        df.at[i,'preprocessed'] = nounss[i]
        
    for i in range(len(df)):
        if 'tagesschau' in df.loc[i,'transcriptionName'] and 'vor' not in df.loc[i,'transcriptionName']:
            df.at[i,'year'] = int((df.loc[i,'transcriptionName'].split('_')[1][4:8]))
    #display(df.head(10))
    return df,df1

def print_workcloud(processed_transcripts):
    
    # used from tutorial to create a workcloud
    all_documents_as_one_string = ','.join(list(processed_transcripts.values))
    print(len(all_documents_as_one_string))
    #all_documents_as_one_string = ','.join(list(df['content'].values))
    wordcloud = WordCloud(width=800,height=400,background_color="black", max_words=500, contour_width=3, contour_color='steelblue')
    wordcloud.generate(all_documents_as_one_string)
    time.sleep(0.3)
    display(wordcloud.to_image())

def plot_25_most_common_words(count_data, count_vectorizer):
    words = count_vectorizer.get_feature_names()
    total_counts = np.zeros(len(words))
    for t in count_data:
        total_counts+=t.toarray()[0]
    
    count_dict = (zip(words, total_counts))
    count_dict = sorted(count_dict, key=lambda x:x[1], reverse=True)[0:25]
    #print((count_dict))
    words = [w[0] for w in count_dict]
    counts = [w[1] for w in count_dict]
    x_pos = np.arange(len(words)) 
    #print(x_pos)
    plt.figure(2, figsize=(15, 15/1.6180))
    plt.subplot(title='25 most common words')
    sns.set_context("notebook", font_scale=1.25, rc={"lines.linewidth": 2.5})
    dfPlot = pd.DataFrame(data={'words':words,'counts':counts})
    #display(dfPlot)
    sns.barplot(x=words,y=counts,data=dfPlot,palette='husl')
    plt.xticks(x_pos, words, rotation=90) 
    plt.xlabel('words')
    plt.ylabel('counts')
    plt.show()


def print_topics(model, count_vectorizer, n_top_words):
    words = count_vectorizer.get_feature_names()
    for topic_idx, topic in enumerate(model.components_):
        print("Topic #%d:" % (int(topic_idx)+1)," ".join([words[i] for i in topic.argsort()[:-n_top_words - 1:-1]]))
    

def train_lda_sklearn(df,count_vectorizer,count_data,number_topics=10,number_words=3,ngram_tuple=(1,1),stop_words=None):#stopwords.words('german'))
    # n_jobs=-1 to use all processors, max_iter=50 randomly chosen, not sure about it
    lda = LDA(n_components=n_topics, n_jobs=-1)
    lda.fit(count_data)
    print("LDA Topics:")
    print_topics(lda, count_vectorizer, n_words)
    return lda

def train_model_gensim(df,num_topics=20,passes=10,workers=int((os.cpu_count()/2))-1):
    for i in range(len(df['preprocessed'])):
        df.at[i,'preprocessed'] = df.loc[i,'preprocessed'].split(" ")
    dictionary = corpora.Dictionary(df['preprocessed'])
    bow_corpus = [dictionary.doc2bow(doc) for doc in df['preprocessed']]
    lda_model = models.LdaMulticore(bow_corpus, num_topics=num_topics, id2word=dictionary, passes=passes, workers=workers)
    return lda_model, bow_corpus, dictionary
    

print("done")

done


In [8]:
#%%time
############################### preprocess and train for each year separately for a given daterange ####################################


path = "/home/sim/all/Master/Forschungspraktikum/Tagesschau/transcripts/"
n_cpu_cores = 13 #int(os.cpu_count()-1)
print("number cpu_cores to use:",n_cpu_cores)

#load s2t transcriptions
path = "/home/sim/all/Master/Forschungspraktikum/Tagesschau/transcripts/"
transcriptions = load_transcriptions(path)
keys = ['2007','2008','2009','2010','2011','2012','2013','2014','2015','2016','2017','2018','2019','2020']
years_dict = {}
for year in keys: 
    years_dict[year] = []

# lda for certain dates
daterange = pd.date_range(datetime.datetime(2007, 1, 1), datetime.datetime(2020, 7, 31))
dates_of_interest = []
for date in daterange:
    for i in transcriptions:
        if 'tagesschau' in i and 'vor' not in i:
            year = int((i.split('_')[1][4:8]))
            if year==date.year:
                month = int((i.split('_')[1][2:4]))
                if month == date.month:
                    day = int((i.split('_')[1][0:2]))
                    if day == date.day:
                        years_dict[str(year)].append(i)
                        dates_of_interest.append(i)
print("There are ",len(dates_of_interest),"transcriptions in given daterange")

#"""
for year in years_dict.keys():
    print("\npreprocess transcriptions of year:",year,"quantity:",len(years_dict[str(year)]))
    if len(years_dict[str(year)]) == 0:
        print("no transcription for year:",year)
        continue
    start = datetime.datetime.now()
    #transcriptions = transcriptions[i*50:(i+1)*50]
    transcriptions = years_dict[str(year)]
    # maybe: more threads -> more RAM so in case of low ram use less cores


    df_processed,df1 = preprocess_transcriptions(transcriptions,number_cpu_cores=n_cpu_cores)
    #print_workcloud(df_processed['preprocessed'])

    # Initialise count vectorizer
    count_vectorizer = CountVectorizer(ngram_range=(1,1))
    # Fit and transform the processed titlest
    count_data = count_vectorizer.fit_transform(df_processed['preprocessed'])
    #params for LDA
    n_topics = 10 #alpha
    n_words = 5 #beta

    # Visualise the 10 most common words
    #plot_25_most_common_words(count_data, count_vectorizer)
    
    #"""
    # with gensim lda
    startLDA = datetime.datetime.now()
    lda_model,bow_corpus,dictionary = train_model_gensim(df=df_processed,num_topics=20,passes=10,workers=7)
    endLDA = datetime.datetime.now()
    print("lda training needs:",(endLDA-startLDA).total_seconds(),"seconds")
    for idx, topic in lda_model.print_topics(-1):
        print('Topic: {} \nWords: {}'.format(idx+1, re.sub('[^A-Za-z ]+', '', topic).replace("  "," ")))
    
    #"""
    """
    # with sklearn lda
    lda_model = train_lda_sklearn(df_processed,count_vectorizer,count_data,number_topics=n_topics,number_words=n_words,ngram_tuple=(2,3),stop_words=None)
    print_topics(lda_model, count_vectorizer, n_words)
    del df_processed
    del count_data
    del lda_model
    #print("loop needed:",(end-start).total_seconds(),"seconds")
    #"""
    startVis = datetime.datetime.now()
    display(pyLDAvis.gensim.prepare(lda_model, bow_corpus, dictionary))
    endVis = datetime.datetime.now()
    print((endVis-startVis).total_seconds(),"seconds")

#"""

number cpu_cores to use: 13
There are  3765 transcriptions in given daterange

preprocess transcriptions of year: 2007 quantity: 263
lemmatizing+filtering out nouns needs: 20.621717 seconds
replacing e.g. 'sonne','regen'... by 'wetter' needs: 0.677988 seconds
lda training needs: 22.693536 seconds
Topic: 1 
Words: berlin polizei gewerkschaft gericht treffen usa gdl bahn peking gipfel
Topic: 2 
Words: spd bahn merkel gipfel polizei heiligendamm cdu partei kanzlerin gdl
Topic: 3 
Words: treffen union cdu fdp bahn heftige olympischen risse beton anschlaege
Topic: 4 
Words: spd urlaub gilt hamburger gdl weiterbildung mindestlohn scheint frankreich bau
Topic: 5 
Words: spd bahn soldaten berlin merkel gdl kinder muenchen gipfel einsatz
Topic: 6 
Words: bahn kanzlerin spd berlin kinder trotz china laender fordern bekommen
Topic: 7 
Words: kinder merkel spd gewerkschaft oettinger stark polizei afghanistan cdu csu
Topic: 8 
Words: berlin spd polizei partei kinder merkel sarkozy union afghanistan

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
19     0.104813  0.008826       1        1  15.763495
10     0.108136  0.002213       2        1  15.151265
7      0.103854  0.001211       3        1  11.103715
14     0.102121  0.014621       4        1   9.365797
1      0.104344 -0.002755       5        1   8.900806
...         ...       ...     ...      ...        ...
11    -0.082349  0.010535      16        1   1.428938
18    -0.112925  0.011882      17        1   0.990385
2     -0.104126 -0.005901      18        1   0.895082
9     -0.135071  0.006185      19        1   0.764444
13    -0.147803 -0.004098      20        1   0.334994

[20 rows x 5 columns], topic_info=               Term        Freq       Total Category  logprob  loglift
982             spd  426.000000  426.000000  Default  30.0000  30.0000
536     afghanistan  247.000000  247.000000  Default  29.0000  29.0000
2388          putin  142.000000  142.000000  Default  28.0000  28.0000
7902           bahn  335.000000  335.000000  Default  27.0000  27.0000
3924    mindestlohn  193.000000  193.000000  Default  26.0000  26.0000
...             ...         ...         ...      ...      ...      ...
1957      schaeuble    0.542018   94.505951  Topic20  -7.1095   0.5377
1258         faellt    0.541796  140.893402  Topic20  -7.1100   0.1379
786   innenminister    0.541367   87.584122  Topic20  -7.1107   0.6126
195          glaube    0.541250  109.175507  Topic20  -7.1110   0.3920
1422          namen    0.540670   68.119820  Topic20  -7.1120   0.8626

[1633 rows x 6 columns], token_table=       Topic      Freq          Term
term                                
26518     17  0.807273      abfangen
4782       1  0.127450  abgeordneten
4782       2  0.280390  abgeordneten
4782       3  0.076470  abgeordneten
4782       4  0.101960  abgeordneten
...      ...       ...           ...
22819     12  0.380401         zuzug
22819     17  0.190200         zuzug
13611      3  0.851994    zuzuordnen
33868      8  0.737271   zwangsweise
33868     10  0.245757   zwangsweise

[6145 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[20, 11, 8, 15, 2, 5, 16, 17, 1, 7, 9, 6, 18, 4, 13, 12, 19, 3, 10, 14])

14.325941 seconds

preprocess transcriptions of year: 2008 quantity: 358
lemmatizing+filtering out nouns needs: 28.373154 seconds
replacing e.g. 'sonne','regen'... by 'wetter' needs: 0.952064 seconds
lda training needs: 31.465592 seconds
Topic: 1 
Words: maschine daten bolivien bank einigung treffen schwere piraten russischen buerger
Topic: 2 
Words: unicef urteil koalition kirche stellen union daten private bundesinnenminister forschung
Topic: 3 
Words: spd waffenruhe mieter spiel stadt kinder patientenverfuegung wasser vermieter loew
Topic: 4 
Words: berlin polizei soldaten spd mitte merkel politik hilfe bundestag israel
Topic: 5 
Words: spd cdu berlin obama fdp partei polizei koalition stadt afghanistan
Topic: 6 
Words: gazastreifen israel hamas palaestinenser aussenminister partei israelische georgien cdu kinder
Topic: 7 
Words: spd usa union berlin obama partei eu koalition merkel melden
Topic: 8 
Words: spd haelfte nordkorea beck piraten usa banken aufgabe partei kurt
Topic: 9 
W

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
6      0.147546 -0.001174       1        1  45.449902
3      0.127726  0.007284       2        1   9.630804
4      0.134770 -0.007866       3        1   9.263370
16     0.123387 -0.006197       4        1   7.261352
13     0.107562  0.013592       5        1   5.256095
...         ...       ...     ...      ...        ...
2     -0.092163  0.034257      16        1   0.884355
1     -0.123012  0.017543      17        1   0.540498
17    -0.150358  0.004106      18        1   0.108960
14    -0.158207  0.002979      19        1   0.100353
9     -0.148347  0.002044      20        1   0.009373

[20 rows x 5 columns], topic_info=           Term        Freq       Total Category  logprob  loglift
1029        spd  762.000000  762.000000  Default  30.0000  30.0000
3734     israel  272.000000  272.000000  Default  29.0000  29.0000
900      merkel  338.000000  338.000000  Default  28.0000  28.0000
501       union  413.000000  413.000000  Default  27.0000  27.0000
134          eu  372.000000  372.000000  Default  26.0000  26.0000
...         ...         ...         ...      ...      ...      ...
677         cdu    0.001273  297.543243  Topic20  -9.9158  -3.0872
682         csu    0.001255  265.746002  Topic20  -9.9296  -2.9880
1889  koalition    0.001212  325.891663  Topic20  -9.9646  -3.2270
900      merkel    0.001195  338.078156  Topic20  -9.9785  -3.2776
310      melden    0.001186  308.592957  Topic20  -9.9864  -3.1943

[1606 rows x 6 columns], token_table=       Topic      Freq          Term
term                                
13366     16  0.599983  abfangrakete
11043      1  0.498838  abgeordneten
11043      2  0.160341  abgeordneten
11043      3  0.071263  abgeordneten
11043      4  0.053447  abgeordneten
...      ...       ...           ...
2126      13  0.006914         zuvor
2126      14  0.006914         zuvor
2126      15  0.006914         zuvor
20550      5  0.929702  zwangsarbeit
30383      2  0.955731  zweitstimmen

[4993 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[7, 4, 5, 17, 14, 20, 13, 19, 16, 6, 11, 1, 12, 8, 9, 3, 2, 18, 15, 10])

17.429537 seconds

preprocess transcriptions of year: 2009 quantity: 358
lemmatizing+filtering out nouns needs: 28.768824 seconds
replacing e.g. 'sonne','regen'... by 'wetter' needs: 1.002378 seconds
lda training needs: 29.240532 seconds
Topic: 1 
Words: porsche laender internet strom windows berlin zukunft sri entschieden strasse
Topic: 2 
Words: spd eu partei internet usa entscheidung berlin israel afghanistan opel
Topic: 3 
Words: internet obama opposition getoetet usa afghanistan zb polizei faellt bericht
Topic: 4 
Words: winnenden schueler waffen polizei nato lehrer memorial frankreich besucher verhindern
Topic: 5 
Words: spd arbeit berlin kurzarbeit polizei obama cdu union vertrag fdp
Topic: 6 
Words: fdp berlin spd obama union laender cdu usa freiheit merkel
Topic: 7 
Words: opel motors general magna berlin bund entscheidung laender bahn csu
Topic: 8 
Words: porsche vw spd volkswagen nato ahmadinedschad regime ergebnis bundesrat schule
Topic: 9 
Words: israel gazastreifen hamas 

...

16.605192 seconds

preprocess transcriptions of year: 2017 quantity: 51
lemmatizing+filtering out nouns needs: 3.841191 seconds
replacing e.g. 'sonne','regen'... by 'wetter' needs: 0.146075 seconds
lda training needs: 5.672419 seconds
Topic: 1 
Words: cdu polen afd wahlkampf sicherheit usa wahlprogramm facebook trump holm
Topic: 2 
Words: trump eu usa fluechtlinge museum italien obama libyen opfer tunesien
Topic: 3 
Words: polizei steinmeier trump behoerden berlin amri koeln personen entscheidung wissen
Topic: 4 
Words: muenchen nato trump laender sicherheitskonferenz erdogan internationalen leipzig merkel fuehrung
Topic: 5 
Words: trump merkel spd afghanistan usa partei laender eu kinder behoerden
Topic: 6 
Words: wasser vw platz berlin gabriel trump neuer usa herzog spd
Topic: 7 
Words: npd trump nato eu usa fluechtlinge schulz zusammenarbeit partei dahlmeier
Topic: 8 
Words: trump berlin cdu donald steinbach amri urteil falschmeldungen bericht washington
Topic: 9 
Words: nawalny ver

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
13     0.133076 -0.017387       1        1  14.986486
11     0.126982 -0.010224       2        1  11.257353
5      0.048130  0.163296       3        1   9.192461
2      0.087677  0.087704       4        1   9.130048
10     0.076360 -0.039889       5        1   8.909462
...         ...       ...     ...      ...        ...
0     -0.084555  0.009001      16        1   1.964003
16    -0.091941  0.006604      17        1   0.247907
8     -0.087504  0.005874      18        1   0.221502
18    -0.072733  0.004863      19        1   0.006403
4     -0.071192  0.005092      20        1   0.006403

[20 rows x 5 columns], topic_info=            Term       Freq      Total Category  logprob  loglift
761          cdu  33.000000  33.000000  Default  30.0000  30.0000
6481      schulz  42.000000  42.000000  Default  29.0000  29.0000
1606      partei  56.000000  56.000000  Default  28.0000  28.0000
6719         npd  18.000000  18.000000  Default  27.0000  27.0000
3033        nato  37.000000  37.000000  Default  26.0000  26.0000
...          ...        ...        ...      ...      ...      ...
529       studio   0.000228  41.387379  Topic20  -9.3199  -2.4511
429   polizisten   0.000227  28.213669  Topic20  -9.3255  -2.0734
840      gabriel   0.000228  42.735687  Topic20  -9.3219  -2.4851
1172       union   0.000228  44.663609  Topic20  -9.3222  -2.5295
474     schoenen   0.000227  39.069393  Topic20  -9.3245  -2.3980

[1432 rows x 6 columns], token_table=      Topic      Freq           Term
term                                
8379     12  0.771332  abgeschlossen
3         4  0.877568       ablaeufe
5398      4  0.297932    abschaffung
5398      5  0.297932    abschaffung
5398     16  0.297932    abschaffung
...     ...       ...            ...
8090      4  0.395492         zverev
8090     12  0.593237         zverev
7048     13  0.825862    zweistellig
4335      7  0.288112         zypern
4335     12  0.576223         zypern

[3304 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[14, 12, 6, 3, 11, 7, 10, 2, 8, 20, 13, 16, 18, 15, 4, 1, 17, 9, 19, 5])

5.217608 seconds

preprocess transcriptions of year: 2018 quantity: 0
no transcription for year: 2018

preprocess transcriptions of year: 2019 quantity: 0
no transcription for year: 2019

preprocess transcriptions of year: 2020 quantity: 208
lemmatizing+filtering out nouns needs: 17.150638 seconds
replacing e.g. 'sonne','regen'... by 'wetter' needs: 0.585062 seconds
lda training needs: 21.148904 seconds
Topic: 1 
Words: corona eu cdu union afd berlin usa coronavirus iran pandemie
Topic: 2 
Words: corona quarantaene italien coronavirus pandemie kunden polen bahn tuerkei lage
Topic: 3 
Words: corona pandemie union berlin polizei trump quarantaene partei app laender
Topic: 4 
Words: coronavirus virus berlin china union thueringen partei trump amt hertha
Topic: 5 
Words: china iran bleiben usa trump irak us putin parlament kraftwerke
Topic: 6 
Words: corona tuerkei eu fluechtlinge polizei bundeswehr trump frage china grenze
Topic: 7 
Words: corona pandemie coronavirus eu massnahmen virus b

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
10    -0.105545 -0.006898       1        1  17.543074
6     -0.111572  0.004512       2        1  16.956053
19    -0.100711  0.012920       3        1  10.391747
0     -0.094413 -0.049060       4        1   9.651570
12    -0.070946  0.062053       5        1   5.895539
...         ...       ...     ...      ...        ...
1      0.066914  0.017160      16        1   1.485349
17     0.090099  0.009977      17        1   1.433894
4      0.114988  0.015001      18        1   1.018392
14     0.118108 -0.001720      19        1   0.872945
13     0.173651  0.017890      20        1   0.127571

[20 rows x 5 columns], topic_info=             Term         Freq        Total Category  logprob  loglift
9951       corona  1294.000000  1294.000000  Default  30.0000  30.0000
2279          cdu   210.000000   210.000000  Default  29.0000  29.0000
555         trump   236.000000   236.000000  Default  28.0000  28.0000
303          iran   103.000000   103.000000  Default  27.0000  27.0000
1361        china   194.000000   194.000000  Default  26.0000  26.0000
...           ...          ...          ...      ...      ...      ...
952        kosten     0.154735    80.397247  Topic20  -7.2237   0.4112
5714     forscher     0.139856    21.146473  Topic20  -7.3248   1.6456
2700       bundes     0.142304    47.030216  Topic20  -7.3075   0.8637
9823   politikers     0.126921     5.062913  Topic20  -7.4219   2.9781
6072  jahrzehnten     0.124651    16.552601  Topic20  -7.4399   1.7755

[1618 rows x 6 columns], token_table=       Topic      Freq        Term
term                              
19672      1  0.833314  abenteurer
10112      2  0.196740     abfahrt
10112      5  0.196740     abfahrt
10112      7  0.196740     abfahrt
10112     11  0.196740     abfahrt
...      ...       ...         ...
1818      19  0.011576       zuvor
9651       2  0.427366      zverev
9651      15  0.427366      zverev
16486      3  0.350390     zwickau
16486     16  0.350390     zwickau

[5767 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[11, 7, 20, 1, 13, 19, 6, 17, 3, 8, 4, 10, 9, 16, 12, 2, 18, 5, 15, 14])

11.94631 seconds


In [7]:
#%%time
################### preprocess data for given daterange in yearly portions for feasibility in terms of RAM usage #######################
################### train on whole data afterwards #############################################################################################

path = "/home/sim/all/Master/Forschungspraktikum/Tagesschau/transcripts/"
n_cpu_cores = 13 #int(os.cpu_count()-1)
print("number cpu_cores to use:",n_cpu_cores)
df_all_processed = pd.DataFrame(index=[], columns=['preprocessed'])
#display(df_all_processed)

#load s2t transcriptions
path = "/home/sim/all/Master/Forschungspraktikum/Tagesschau/transcripts/"
transcriptions = load_transcriptions(path)
keys = ['2007','2008','2009','2010','2011','2012','2013','2014','2015','2016','2017','2018','2019','2020']
years_dict = {}
for year in keys: 
    years_dict[year] = []

# prepare daterange of interest for lda
daterange = pd.date_range(datetime.datetime(2007, 1, 1), datetime.datetime(2020, 12, 31))
dates_of_interest = []
for date in daterange:
    for i in transcriptions:
        if 'tagesschau' in i and 'vor' not in i:
            #print(i)
            year = int((i.split('_')[1][4:8]))
            if year==date.year:
                month = int((i.split('_')[1][2:4]))
                if month == date.month:
                    day = int((i.split('_')[1][0:2]))
                    if day == date.day:
                        years_dict[str(year)].append(i)
                        dates_of_interest.append(i)
print("There are ",len(dates_of_interest),"transcriptions in given daterange")

# preprocess every year
for year in years_dict.keys():
    print("\npreprocess transcriptions of year:",year,"quantity:",len(years_dict[str(year)]))
    if len(years_dict[str(year)]) == 0:
        print("no transcription for year:",year)
        continue
    start = datetime.datetime.now()
    transcriptions = years_dict[str(year)]
    df_processed,df1 = preprocess_transcriptions(transcriptions,number_cpu_cores=n_cpu_cores)
    df_all_processed['preprocessed'] = df_all_processed['preprocessed'].append(df_processed['preprocessed'],ignore_index=True)
    

# Initialise count vectorizer
count_vectorizer = CountVectorizer(ngram_range=(1,1))

# Fit and transform the processed titles
count_data = count_vectorizer.fit_transform(df_all_processed['preprocessed'])

#params for LDA
n_topics = 10 #alpha
n_words = 5 #beta

# Visualise the 25 most common words
#plot_25_most_common_words(count_data, count_vectorizer)

# with gensim lda
print("Train LDA...")
startLDA = datetime.datetime.now()
lda_model,bow_corpus,dictionary = train_model_gensim(df=df_all_processed,num_topics=20,passes=10,workers=7)
endLDA = datetime.datetime.now()
print("lda training needs:",(endLDA-startLDA).total_seconds(),"seconds")
for idx, topic in lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx+1, re.sub('[^A-Za-z ]+', '', topic).replace("  "," ")))
#"""
"""
# with sklearn lda
lda_model = train_lda_sklearn(df_processed,count_vectorizer,count_data,number_topics=n_topics,number_words=n_words,ngram_tuple=(2,3),stop_words=None)
print_topics(lda_model, count_vectorizer, n_words)
del df_processed
del count_data
del lda_model
#print("loop needed:",(end-start).total_seconds(),"seconds")
#"""
#"""
startVis = datetime.datetime.now()
display(pyLDAvis.gensim.prepare(lda_model, bow_corpus, dictionary))
endVis = datetime.datetime.now()
print((endVis-startVis).total_seconds(),"seconds")

print("\ndone")

number cpu_cores to use: 13
There are  3878 transcriptions in given daterange

preprocess transcriptions of year: 2007 quantity: 263
lemmatizing+filtering out nouns needs: 20.721334 seconds
replacing e.g. 'sonne','regen'... by 'wetter' needs: 0.681707 seconds

preprocess transcriptions of year: 2008 quantity: 358
lemmatizing+filtering out nouns needs: 30.149627 seconds
replacing e.g. 'sonne','regen'... by 'wetter' needs: 0.995603 seconds

preprocess transcriptions of year: 2009 quantity: 358
lemmatizing+filtering out nouns needs: 29.487958 seconds
replacing e.g. 'sonne','regen'... by 'wetter' needs: 0.985858 seconds

preprocess transcriptions of year: 2010 quantity: 357
lemmatizing+filtering out nouns needs: 27.983322 seconds
replacing e.g. 'sonne','regen'... by 'wetter' needs: 0.912645 seconds

preprocess transcriptions of year: 2011 quantity: 353
lemmatizing+filtering out nouns needs: 28.276387 seconds
replacing e.g. 'sonne','regen'... by 'wetter' needs: 0.913597 seconds

preprocess 

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
12     0.147313 -0.006224       1        1  33.922997
3      0.132174 -0.033423       2        1  12.266665
15     0.124759  0.044783       3        1   9.637548
19     0.115569 -0.038922       4        1   8.656331
6      0.091000 -0.006971       5        1   5.958660
...         ...       ...     ...      ...        ...
5     -0.078779 -0.004322      16        1   1.067322
8     -0.100506  0.011223      17        1   1.004615
17    -0.119859 -0.022682      18        1   0.553099
7     -0.157024  0.008201      19        1   0.169094
0     -0.157080  0.007224      20        1   0.166207

[20 rows x 5 columns], topic_info=              Term        Freq       Total Category  logprob  loglift
982            spd  433.000000  433.000000  Default  30.0000  30.0000
1574         union  302.000000  302.000000  Default  29.0000  29.0000
7902          bahn  344.000000  344.000000  Default  28.0000  28.0000
536    afghanistan  258.000000  258.000000  Default  27.0000  27.0000
404       soldaten  238.000000  238.000000  Default  26.0000  26.0000
...            ...         ...         ...      ...      ...      ...
20698   staerkeren    0.230278    5.497052  Topic20  -7.2647   3.2270
9846     regisseur    0.243216    9.842636  Topic20  -7.2100   2.6992
5370    abschnitte    0.234020   10.623669  Topic20  -7.2486   2.5843
12155    laengerem    0.190069    7.196402  Topic20  -7.4566   2.7657
7907      belastet    0.193679   13.016679  Topic20  -7.4378   2.1919

[1542 rows x 6 columns], token_table=       Topic      Freq              Term
term                                    
27597     12  0.516671         abgehoben
11297     17  0.851836  abgeschiedenheit
17975      1  0.876869        abschlaege
25167      3  0.242566       abschmelzen
25167     12  0.727699       abschmelzen
...      ...       ...               ...
6583      14  0.349940      zurueckgehen
4420       9  0.468889      zusammenhalt
29058     13  0.540153    zusammenhalten
35952     15  0.578147          zusetzen
9033       7  0.843443            zweien

[5076 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[13, 4, 16, 20, 7, 10, 5, 3, 11, 2, 12, 15, 19, 14, 17, 6, 9, 18, 8, 1])

15.630298 seconds

done


In [ ]:
#%%time 
#lda_model = models.LdaMulticore(bow_corpus, num_topics=20, id2word=dictionary, passes=100, workers=7)
#for idx, topic in lda_model.print_topics(-1):
#    print('Topic: {} \nWords: {}'.format(idx+1, re.sub('[^A-Za-z ]+', '', topic).replace("  "," ")))

In [ ]:
#%%time 
#display(pyLDAvis.gensim.prepare(lda_model, bow_corpus, dictionary))